#Tier at purchase/pyspark

In [0]:
from pyspark.sql import SparkSession, functions as F
from pyspark.sql.functions import col, max, when, lag, to_date, coalesce, row_number, lit, year, month
from pyspark.sql.window import Window
from ipywidgets import widgets
import matplotlib.pyplot as plt
##from IPython.display import display
##import networkx as nx ## need to install networkx to cluster to enable visualizations


In [0]:
spark.conf.set("spark.sql.execution.arrow.enabled", "true")

members_loyalty_engagements = spark.table("cadp_consumer_sciences_lh.members_loyalty_engagements")
members_loyalty_tiers = spark.table("cadp_consumer_sciences_lh.members_loyalty_tiers")
consumer_profile = spark.table("cadp_consumer_sciences_lh.consumer_profile")
members_loyalty_expired_asset = spark.table("cadp_consumer_sciences_lh.members_loyalty_expired_asset")


In [0]:
# First, filter the consumer_profile DataFrame for non-null loyalty_memberid
consumer_profile_filtered = consumer_profile.filter(consumer_profile.loyalty_memberid.isNotNull())

# Join operations, ensuring we use aliases and specify columns unambiguously
tier_info = members_loyalty_engagements.alias('l') \
    .join(members_loyalty_tiers.alias('t'), 'acid', 'left_outer') \
    .join(consumer_profile_filtered.alias('cp'), 'acid', 'inner') \
    .filter((F.col('l.order_number').isNotNull()) & (F.col('l.engagement_date') > '2018-01-01')) \
    .groupBy('l.acid', 'l.order_number') \
    .agg(
        F.max('l.tier_details_id').alias('tier_after_purchase'),
        F.max(F.when(F.col('t.tier_achieved_date') <= F.col('l.engagement_date'), F.col('t.tier_details_id'))).alias('tier_before_purchase_raw'),
        F.max(F.when(F.col('t.tier_achieved_date') <= F.col('l.engagement_date'), F.col('t.tier_achieved_date'))).alias('tier_date'),
        F.max('l.engagement_date').alias('order_date'),
        F.first('t.country_code').alias('country_code')  # Adding country_code
    )

# Window specification for calculating previous order date and tier
windowSpec = Window.partitionBy('acid').orderBy('order_date')

# Calculating previous order date and tier
previous_order_date = tier_info.withColumn('prev_order_date', F.lag('order_date').over(windowSpec)) \
    .withColumn('prev_tier_after_purchase', F.lag('tier_after_purchase').over(windowSpec))

# Joining with members_loyalty_expired_asset for expired_assets
expired_assets = previous_order_date.alias('p') \
    .join(members_loyalty_expired_asset.alias('ea'), (F.col('p.acid') == F.col('ea.acid')) & (F.col('ea.expiry_date') > F.col('p.prev_order_date')) & (F.col('ea.expiry_date') <= F.col('p.order_date')), 'left_outer') \
    .select('p.acid', 'p.country_code', 'p.order_number', 'p.order_date', 'p.prev_order_date', 'p.tier_after_purchase', 'p.tier_before_purchase_raw', 'p.tier_date', 'p.prev_tier_after_purchase', F.col('ea.asset_type').alias('neg_tier_movement'))

# Assigning row numbers to orders
ranked_orders = expired_assets.withColumn('rn', F.row_number().over(windowSpec))

# Final selection and transformation
final_df = ranked_orders.select(
    'acid',
    'order_number',
    'country_code',  # Added here
    'tier_after_purchase',
    F.to_date('tier_date').alias('tier_date'),
    F.to_date('order_date').alias('order_date'),
    F.coalesce('tier_before_purchase_raw', F.lit(0)).alias('tier_before_purchase'),
    F.when(F.col('rn') == 1, 'first_purchase')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) < F.coalesce('tier_after_purchase', F.lit(0)), 'Upgrade')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) > F.coalesce('tier_after_purchase', F.lit(0)), 'Downgrade')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) == F.coalesce('tier_after_purchase', F.lit(0)), 'No Change')
    .otherwise('subsequent_purchase').alias('action_before_purchase'),
    F.max('neg_tier_movement').over(Window.partitionBy('acid', 'order_number')).alias('neg_tier_movement')
)

# Optional: Creating a temporary view for SQL-like querying
final_df.createOrReplaceTempView("tier_at_purchase")

#Examples

In [0]:
specific_user_df = spark.sql("SELECT * FROM tier_at_purchase WHERE acid = '004K2KV4OEU0OCOB'")
display(specific_user_df)

acid order_number country_code tier_after_purchase tier_date order_date tier_before_purchase action_before_purchase neg_tier_movement 004K2KV4OEU0OCOB 448900000001010000000000000004230513042022 GB 2 2021-11-14 2022-04-13 2 No Change null 004K2KV4OEU0OCOB AUK30094161 GB 0 null 2020-11-28 0 first_purchase null 004K2KV4OEU0OCOB AUK31207140 GB 0 null 2020-12-20 0 No Change null 004K2KV4OEU0OCOB AUK35386658 GB 1 null 2021-04-21 0 Upgrade null 004K2KV4OEU0OCOB AUK38693067 GB 1 2021-04-23 2021-07-27 1 No Change null 004K2KV4OEU0OCOB AUK38711593 GB 1 2021-04-23 2021-07-27 1 No Change null 004K2KV4OEU0OCOB AUK39164693 GB 1 2021-04-23 2021-08-02 1 No Change null 004K2KV4OEU0OCOB AUK43530463 GB 2 2021-04-23 2021-11-13 1 Upgrade null 004K2KV4OEU0OCOB AUK44125502 GB 2 2021-11-14 2021-11-23 2 No Change null 004K2KV4OEU0OCOB AUK47305665 GB 2 2021-11-14 2022-02-18 2 No Change null 004K2KV4OEU0OCOB AUK50279347 GB 2 2021-11-14 2022-05-14 2 No Change null 004K2KV4OEU0OCOB AUK52476801 GB 2 2021-11-14 2022-07-05 2 No Change null 004K2KV4OEU0OCOB AUK52705796 GB 2 2021-11-14 2022-07-10 2 No Change null 004K2KV4OEU0OCOB AUK55440235 GB 2 2021-11-14 2022-09-15 2 No Change null 004K2KV4OEU0OCOB AUK57214803 GB 2 2021-11-14 2022-10-28 2 No Change null 004K2KV4OEU0OCOB AUK64058757 GB 1 2022-12-01 2023-05-10 2 Downgrade TIER 004K2KV4OEU0OCOB AUK65941594 GB 1 2022-12-01 2023-07-13 2 Downgrade null 004K2KV4OEU0OCOB AUK69125455 GB 1 2022-12-01 2023-11-17 2 Downgrade null

In [0]:

# Filter for upgrades in January in the US and CA
upgrades_in_jan_us_ca = final_df.filter(
    (final_df.action_before_purchase == 'Upgrade') & 
    (final_df.country_code.isin('US', 'CA')) &
    (month(final_df.order_date) == 1) &
    (year(final_df.order_date) == 2024) 
)

# Count the number of users
count_upgrades = upgrades_in_jan_us_ca.count()

print(f"Number of users who upgraded in January in the US and CA: {count_upgrades}")


Number of users who upgraded in January in the US and CA: 81917


In [0]:
from pyspark.sql import functions as F

# Filter for actions (upgraded, downgraded) in January and group by country and action
actions_count_by_country_jan = final_df.filter(
    (F.col('action_before_purchase').isin(['Upgrade', 'Downgrade'])) &
    (F.month('order_date') == 1)
).groupBy('country_code', 'action_before_purchase').count()

# The resulting DataFrame 'actions_count_by_country_jan' will have columns: country_code, action_before_purchase, and count
# It lists the number of customers who either upgraded or downgraded, categorized by country for the month of January.



In [0]:
display(actions_count_by_country_jan)

country_code action_before_purchase count VN Upgrade 3965 NL Upgrade 16883 IN Downgrade 11220 JP Downgrade 43236 GB Upgrade 125782 IN Upgrade 30769 CO Downgrade 43210 TR Upgrade 31440 DE Upgrade 116985 PH Upgrade 6175 NL Downgrade 11216 PL Downgrade 6485 VN Downgrade 376 DE Downgrade 139275 MY Downgrade 1290 TH Upgrade 12570 SA Upgrade 813 SG Upgrade 16777 IL Upgrade 1332 KR Upgrade 28661 AE Upgrade 3291 UA Downgrade 83361 GB Downgrade 104436 ZA Upgrade 2720 KR Downgrade 9308 EG Upgrade 2290 PH Downgrade 876 PE Downgrade 10745 SG Downgrade 8870 TH Downgrade 1644 ZA Downgrade 240 FR Downgrade 36961 CL Downgrade 16442 IT Downgrade 6209 FR Upgrade 61738 UA Upgrade 37557 ES Downgrade 19006 AE Downgrade 1026 CL Upgrade 26948 US Upgrade 475631 TR Downgrade 7640 EG Downgrade 180 ES Upgrade 40492 CO Upgrade 51039 RU Upgrade 340129 MX Downgrade 41758 PT Upgrade 9 PL Upgrade 11944 BR Downgrade 23928 null Upgrade 45225 BR Upgrade 66059 NZ Upgrade 1563 AU Downgrade 6214 US Downgrade 315259 AR Upgrade 29239 AR Downgrade 11683 MY Upgrade 12572 PE Upgrade 32864 RU Downgrade 455417 MX Upgrade 65276 AU Upgrade 12399 CA Upgrade 26644 CA Downgrade 17020 IT Upgrade 16839 JP Upgrade 77565 NZ Downgrade 710 SA Downgrade 235 IL Downgrade 68 AD Upgrade 1 AT Upgrade 15 PT Downgrade 11 GR Upgrade 4 AT Downgrade 7 GR Downgrade 4 CZ Upgrade 1

In [0]:
us_customer_june = final_df.filter(
    (final_df.country_code.isin('US')) &
    (month(final_df.order_date) == 6) &
    (year(final_df.order_date) == 2023) 
)

In [0]:
display(us_customer_june)

acid order_number country_code tier_after_purchase tier_date order_date tier_before_purchase action_before_purchase neg_tier_movement 007S6K9UE7OVQWTS AD182064073 US 1 2022-06-25 2023-06-18 1 No Change null 007S6K9UE7OVQWTS AD182740729 US 1 2022-06-25 2023-06-24 1 No Change null 007S6K9UE7OVQWTS AD182996645 US 1 2022-06-25 2023-06-27 1 No Change null 007S6K9UE7OVQWTS AD183207967 US 1 2022-06-25 2023-06-29 1 No Change null 00AVXU2QTTTVYL6C AD182749541 US 1 null 2023-06-24 0 first_purchase null 00HFFPKCQXC1QYM3 AD904648941 US 1 null 2023-06-01 0 first_purchase null 00HFFPKCQXC1QYM3 AD905052386 US 1 null 2023-06-01 0 Upgrade null 00ZS4DAQ9QMCB9UF AD905180915 US 1 null 2023-06-01 0 first_purchase null 014QAPH8DYAMQV9Y AD180937829 US 1 null 2023-06-10 0 Upgrade null 01532RJ991XRJ0GU AD905300673 US 2 2023-06-01 2023-06-02 2 No Change null 01HYRDMPW98QP388 AD904678513 US 2 2023-04-20 2023-06-01 1 Upgrade null 01IEJFJZYZNIK9IB AD181346777 US 0 2022-03-02 2023-06-13 1 Downgrade TIER 01J4LXNLPLH59O3A AD181111136 US 1 2023-03-22 2023-06-12 1 No Change null 01MOHJIMO6F3Q3P7 650800000002040000000000000000127601062023 US 3 2022-12-31 2023-06-01 3 No Change null 01PGQ8JZOCF58UCI AD904887060 US 2 null 2023-06-01 0 first_purchase null 01PGQ8JZOCF58UCI AD905001892 US 2 null 2023-06-01 0 Upgrade null 01PGQ8JZOCF58UCI AD905057571 US 2 null 2023-06-01 0 Upgrade null 01PGQ8JZOCF58UCI AD905339747 US 2 2023-06-01 2023-06-02 2 No Change null 01QY57LXZR1RFYMY ADX12165271 US 1 2022-12-20 2023-06-09 1 No Change null 01SSY6LKZGOBPGOB AD181567625 US 1 2023-03-01 2023-06-14 2 Downgrade TIER 01SSY6LKZGOBPGOB AD181794703 US 1 2023-03-01 2023-06-16 2 Downgrade null 01SSY6LKZGOBPGOB AD182047089 US 1 2023-03-01 2023-06-18 2 Downgrade null 01TPT8LON8A3LGBA AD182418764 US 1 2022-11-26 2023-06-21 2 Downgrade null 01VNR18FHVPI77M3 AD181307357 US 1 2022-07-14 2023-06-13 1 No Change null 02A6BOE8WLH7HD9K AD182563693 US 1 null 2023-06-23 0 first_purchase null 02L33R6LUDPSICLD AD904496833 US 3 2023-03-31 2023-06-01 3 No Change null 02L33R6LUDPSICLD AD905426767 US 3 2023-03-31 2023-06-15 3 No Change null 02L33R6LUDPSICLD AD905429537 US 3 2023-03-31 2023-06-15 3 No Change null 02U7P1WS3Z7PPM9F AD181941569 US 1 2022-09-30 2023-06-17 1 No Change null 031QWG09X0LQ9AC9 AD180836368 US 1 2023-06-01 2023-06-09 1 No Change TIER 03GFPV5M8GSGO4SJ 622400000001030000000000000000576330062023 US 2 2023-06-01 2023-06-30 3 Downgrade TIER 03IQDANVAQZXX6B0 AD904451491 US 1 null 2023-06-01 0 first_purchase null 040Q6VXHDYVZ8UI8 AD904603930 US 3 2023-05-31 2023-06-01 1 Upgrade null 040Q6VXHDYVZ8UI8 AD904972665 US 2 2023-05-31 2023-06-01 1 Upgrade null 040Q6VXHDYVZ8UI8 AD905003593 US 2 2023-05-31 2023-06-01 1 Upgrade null 040Q6VXHDYVZ8UI8 AD905087087 US 3 2023-05-31 2023-06-01 1 Upgrade null 040Q6VXHDYVZ8UI8 AD905293040 US 3 2023-06-01 2023-06-02 3 No Change null 0437TF8WJ28EYDGS AD180704237 US 3 2022-09-16 2023-06-08 3 No Change null 048FHTKRYQNQKGIO AD904701575 US 2 2022-08-03 2023-06-01 2 No Change null 04OXVPS7528CECS3 AD905045344 US 1 2022-11-01 2023-06-01 2 Downgrade TIER 04XR6KAO2D697D84 AD182687209 US 2 2022-08-01 2023-06-24 1 Upgrade null 05EBE2HTIMKO4XPM AD180476282 US 2 2022-11-04 2023-06-06 2 No Change null 05KMJ9IML6QKM898 AD181790662 US 1 null 2023-06-16 0 Upgrade null 05LHC1BQ7Q7EGA9Y AD182383086 US 3 2022-11-20 2023-06-21 3 No Change null 05XW0ZLURVV9U1VR AD180145727 US 2 2022-10-16 2023-06-02 2 No Change null 05XW0ZLURVV9U1VR AD180574018 US 2 2022-10-16 2023-06-07 2 No Change null 05XW0ZLURVV9U1VR AD182960929 US 2 2022-10-16 2023-06-27 2 No Change null 061B6R3VDWZED6O0 626400000001020000000000000003739124062023 US 2 2022-11-04 2023-06-24 2 No Change null 06LLH2N52CQNFFF6 620800000001030000000000000002750008062023 US 0 2023-05-31 2023-06-08 1 Downgrade TIER 0784X53BWWFWQUY2 614700000001010000000000000002551625062023 US 1 null 2023-06-25 0 first_purchase null 07D7TEW0CF07R7NM AD904494978 US 2 2023-05-31 2023-06-01 2 No Change null 07GKSF0TCRDPZIIV 615700000001050000000000000003

# Junkyard

**Define needed data sources**

In [0]:
members_loyalty_engagements = spark.table("cadp_consumer_sciences_lh.members_loyalty_engagements")
members_loyalty_tiers = spark.table("cadp_consumer_sciences_lh.members_loyalty_tiers")
consumer_profile = spark.table("cadp_consumer_sciences_lh.consumer_profile")
members_loyalty_expired_asset = spark.table("cadp_consumer_sciences_lh.members_loyalty_expired_asset")

**Implement 'tier_info' Logic**

In [0]:
tier_info = (members_loyalty_engagements
              .join(members_loyalty_tiers, members_loyalty_engagements["acid"] == members_loyalty_tiers["acid"], "left")
              .join(consumer_profile, members_loyalty_engagements["acid"] == consumer_profile["acid"], "left")
              .filter((col("order_number").isNotNull()) & 
                      (consumer_profile["loyalty_memberid"].isNotNull()) & 
                      (col("engagement_date") > "2018-01-01"))
              .groupBy(members_loyalty_engagements["acid"], "order_number", members_loyalty_tiers["country_code"])
              .agg(
                  max(members_loyalty_tiers["tier_details_id"]).alias("tier_after_purchase"),
                  max(when(col("tier_achieved_date") <= col("engagement_date"), members_loyalty_tiers["tier_details_id"])).alias("tier_before_purchase_raw"),
                  max(when(col("tier_achieved_date") <= col("engagement_date"), col("tier_achieved_date"))).alias("tier_date"),
                  max("engagement_date").alias("order_date")
              ))


**Calculate previous_order_date and expired_assets**

In [0]:
windowSpec = Window.partitionBy("acid").orderBy("order_date")

previous_order_date = (tier_info.withColumn("prev_order_date", lag("order_date").over(windowSpec))
                                 .withColumn("prev_tier_after_purchase", lag("tier_after_purchase").over(windowSpec)))

expired_assets = (previous_order_date
                  .join(members_loyalty_expired_asset, "acid", "left")
                  .filter((col("expiry_date") > col("prev_order_date")) & (col("expiry_date") <= col("order_date"))))


**Rank Orders and Select Final Columns**

In [0]:
ranked_orders = expired_assets.withColumn("rn", row_number().over(windowSpec))

final_df = (ranked_orders.select(
            col("acid"),
            col("order_number"),
            col("tier_after_purchase"),
            members_loyalty_tiers["country_code"].alias("country_code"),
            to_date(col("tier_date")).alias("tier_date"),
            to_date(col("order_date")).alias("order_date"),
            coalesce(col("tier_before_purchase_raw"), lit(0)).alias("tier_before_purchase")
            ))


'''final_df = (ranked_orders.select(
            col("acid"),
            "order_number",
            "tier_after_purchase",
            "country_code",
            to_date("tier_date").alias("tier_date"),
            to_date("order_date").alias("order_date"),
            coalesce("tier_before_purchase_raw", lit(0)).alias("tier_before_purchase")
            # Include additional logic for action_before_purchase and neg_tier_movement as needed
            ))'''


'final_df = (ranked_orders.select(\n            col("acid"),\n            "order_number",\n            "tier_after_purchase",\n            "country_code",\n            to_date("tier_date").alias("tier_date"),\n            to_date("order_date").alias("order_date"),\n            coalesce("tier_before_purchase_raw", lit(0)).alias("tier_before_purchase")\n            # Include additional logic for action_before_purchase and neg_tier_movement as needed\n            ))'

In [0]:
final_df.show()

+--------------------+--------------------+-------------------+------------+----------+----------+--------------------+
|                acid|        order_number|tier_after_purchase|country_code| tier_date|order_date|tier_before_purchase|
+--------------------+--------------------+-------------------+------------+----------+----------+--------------------+
|    0005N885XBEY3DFG|         ACL05010849|                  1|          CL|2022-06-23|2023-04-16|                   1|
|    0005N885XBEY3DFG|         ACL05010849|                  1|          CL|2022-06-23|2023-04-16|                   1|
|    0005N885XBEY3DFG|         ACL05010849|                  1|          CL|2022-06-23|2023-04-16|                   1|
|    001BFP2IR94IN20Q|         ADE50254392|                  1|          DE|2022-07-16|2022-09-29|                   1|
|    001BFP2IR94IN20Q|         ADE50254392|                  1|          DE|2022-07-16|2022-09-29|                   1|
|001FF5D5-0104-4A5...|         ANL085098

In [0]:
display(final_df)

acid order_number tier_after_purchase country_code tier_date order_date tier_before_purchase 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 001BFP2IR94IN20Q ADE50254392 1 DE 2022-07-16 2022-09-29 1 001BFP2IR94IN20Q ADE50254392 1 DE 2022-07-16 2022-09-29 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 310100000001010000000000000007902030102022 3 NL 2022-10-26 2022-10-30 2 001KKEH5RTN0FZDT MX14102112450 3 MX 2023-08-01 2024-01-27 3 002A96UXOFOILDZB AD027299077 2 US 2018-10-31 2019-04-24 2 002A96UXOFOILDZB AD027299077 2 US 2018-10-31 2019-04-24 2 002A96UXOFOILDZB AD041607125 2 US 2019-11-06 2019-12-20 2 002A96UXOFOILDZB AD151846693 2 US 2022-01-01 2022-11-11 2 002DSJYV3LSS6915 068-h53sgh0048-i01 3 JP 2018-12-10 2018-12-10 2 002DSJYV3LSS6915 068-h53sgh0048-i01 3 JP 2018-12-10 2018-12-10 2 002DSJYV3LSS6915 068-h53sgh0126-i01 3 JP 2022-06-30 2022-10-19 3 002DSJYV3LSS6915 068-h53sgh0126-i01 3 JP 2022-06-30 2022-10-19 3 002ZXYWLZDFXSH78 ADE51834951 1 DE 2021-08-16 2022-11-14 1 002ZXYWLZDFXSH78 ADE51834951 1 DE 2021-08-16 2022-11-14 1 002ZXYWLZDFXSH78 ADE51834951 1 DE 2021-08-16 2022-11-14 1 003HQNUL48K0IAXQ C24W00000001010000000000000000179910032018 3 RU 2018-02-25 2018-03-09 2 003HQNUL48K0IAXQ C24W00000001010000000000000000179910032018 3 RU 2018-02-25 2018-03-09 2 003HQNUL48K0IAXQ C24W00000001010000000000000002111214072019 3 RU 2019-03-28 2019-07-13 3 003HQNUL48K0IAXQ C24W00000001010000000000000002111214072019 3 RU 2019-03-28 2019-07-13 3 004NXTNQWWFIL6X5 440500000001020000000000000004408421072022 1 GB 2022-07-21 2022-07-21 1 004Y2E2D82IURMTO ABR16501520 1 BR 2022-08-31 2023-11-23 1 006LSAQZPJFIX4A4 AD903649361 2 US 2022-10-22 2023-05-31 1 006LSAQZPJFIX4A4 AD903649361 2 US 2022-10-22 2023-05-31 1 006LSAQZPJFIX4A4 AD903649361 2 US 2022-10-22 2023-05-31 1 008YTIZHIWUNKQBH AD175261019 2 US 2022-06-01 2023-04-16 2 008YTIZHIWUNKQBH AD175261019 2 US 2022-06-01 2023-04-16 2 009BCM6TSC271KW8 AUK28248355 1 GB 2020-07-29 2020-10-19 1 009BCM6TSC271KW8 AUK28248355 1 GB 2020-07-29 2020-10-19 1 009BCM6TSC271KW8 AUK43063400 1 GB 2021-11-01 2021-11-05 1 009BCM6TSC271KW8 AUK62176580 1 GB 2022-08-02 2023-02-26 1 009BCM6TSC271KW8 AUK62176580 1 GB 2022-08-02 2023-02-26 1 009BCM6TSC271KW8 AUK62176580 1 GB 2022-08-02 2023-02-26 1 00DOXQHF6KINJX6M AD045894489 1 US 2020-01-01 2020-02-28 1 00DVC8W1S7915I6M C05200000001010000000000000003344030062019 1 RU 2019-05-29 2019-06-29 1 00DVC8W1S7915I6M C24O00000001020000000000000008886918062021 1 RU 2020-07-01 2021-06-17 1 00E7KL0RM4KFM942 AMX05790955 2 MX 2020-10-05 2020-11-26 2 00E7KL0RM4KFM942 AMX11066729 2 MX 2022-10-31 2022-11-25 2 00EITR8TK2AQJEYT C24L00000001030000000000000008392902082021 1 RU 2020-06-04 2021-08-01 1 00EITR8TK2AQJEYT C24L00000001030000000000000008392902082021 1 RU 2020-06-04 2021-08-01 1 00EYIZ40B1DSWBDD AD113836458 3 US 2021-10-19 2021-10-25 3 00EYIZ40B1DSWBDD AD165109074 3 US 2022-11-01 2023-01-21 3 00GAK33V0QRY73OL ACO04444361 2 CO 2022-07-04 2022-09-02 1 00GQITEDA2JFJELI C03L00000001010000000000000009662707122021 2 RU 2021-10-01 2021-12-06 2 00JNPN13LINQRKWB AUK58293729 2 GB 2022-06-01 2022-11-20 2 00JR8SBNQP6G11X0 AD174965017 2 US 2023-02-01 2023-04-13 2 00JR8SBNQP6G11X0 AD174965017 2 US 2023-02-01 2023-04-13 2 00LGCCTHBSY62QIR 54050 2 BR 2022-12-01 2022-12-04 2 00LGCCTHBSY62QIR BR2270520992 2 BR 2023-12-01 2023-12-19 2 00LMDNFX501EYY3O AD118306975 1 US 2021-04-01 2021-11-30 1 00OMUV6942BLZBAG ATH68077010 1 TH 2022-11-15 2023-06-30 1 00OMUV6942BLZBAG ATH68077010 1 TH 2022-11-15 2023-06-30 1 00OMUV6942BLZBAG ATH68077010 1 TH 2022-11-15 2023-06-30 1 00R3KHXR9P0DWK3U AD915373395 2 US 2023-08-31 2023-10-12 2 00RUA1R1WBMKKKOU ADE18007528 3 DE 2019-

**Create or Replace Temporary View**

In [0]:
final_df.createOrReplaceTempView("tier_at_purchase")


In [0]:
specific_user_df = spark.sql("SELECT * FROM tier_at_purchase WHERE acid = '004K2KV4OEU0OCOB'")
specific_user_df.show()

+----------------+------------+-------------------+------------+----------+----------+--------------------+
|            acid|order_number|tier_after_purchase|country_code| tier_date|order_date|tier_before_purchase|
+----------------+------------+-------------------+------------+----------+----------+--------------------+
|004K2KV4OEU0OCOB| AUK64058757|                  2|          GB|2022-12-01|2023-05-10|                   2|
+----------------+------------+-------------------+------------+----------+----------+--------------------+



In [0]:
%sql
select * 
from tier_at_purchase
limit 10

acid order_number tier_after_purchase country_code tier_date order_date tier_before_purchase 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 0005N885XBEY3DFG ACL05010849 1 CL 2022-06-23 2023-04-16 1 001BFP2IR94IN20Q ADE50254392 1 DE 2022-07-16 2022-09-29 1 001BFP2IR94IN20Q ADE50254392 1 DE 2022-07-16 2022-09-29 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 ANL08509861 3 NL 2022-04-25 2022-06-02 1 001FF5D5-0104-4A58-0B90-97F7B5B52902 310100000001010000000000000007902030102022 3 NL 2022-10-26 2022-10-30 2 001KKEH5RTN0FZDT MX14102112450 3 MX 2023-08-01 2024-01-27 3

In [0]:
from pyspark.sql import SparkSession, functions as F
from pyspark.sql.functions import max, col, lag, to_date, coalesce, row_number, when
from pyspark.sql.window import Window

# Initialize Spark Session (assuming it's already created)
spark = SparkSession.builder.appName("Loyalty Tier Analysis").getOrCreate()

# Assuming DataFrame representations of your SQL tables are already loaded or created, e.g.:
# members_loyalty_engagements, members_loyalty_tiers, consumer_profile, members_loyalty_expired_asset

members_loyalty_engagements = spark.table("cadp_consumer_sciences_lh.members_loyalty_engagements")
members_loyalty_tiers = spark.table("cadp_consumer_sciences_lh.members_loyalty_tiers")
consumer_profile = spark.table("cadp_consumer_sciences_lh.consumer_profile")
members_loyalty_expired_asset = spark.table("cadp_consumer_sciences_lh.members_loyalty_expired_asset")

# tier_info CTE

tier_info = (members_loyalty_engagements
              .join(members_loyalty_tiers, members_loyalty_engagements["acid"] == members_loyalty_tiers["acid"], "left")
              .join(consumer_profile, members_loyalty_engagements["acid"] == consumer_profile["acid"], "left")
              .filter((col("order_number").isNotNull()) & 
                      (consumer_profile["loyalty_memberid"].isNotNull()) & 
                      (col("engagement_date") > "2018-01-01"))
              .groupBy(members_loyalty_engagements["acid"], "order_number", members_loyalty_tiers["country_code"])
              .agg(
                  max(members_loyalty_tiers["tier_details_id"]).alias("tier_after_purchase"),
                  max(when(col("tier_achieved_date") <= col("engagement_date"), members_loyalty_tiers["tier_details_id"])).alias("tier_before_purchase_raw"),
                  max(when(col("tier_achieved_date") <= col("engagement_date"), col("tier_achieved_date"))).alias("tier_date"),
                  max("engagement_date").alias("order_date")
              ))


# previous_order_date CTE
windowSpec = Window.partitionBy("acid").orderBy("order_date")
previous_order_date = (tier_info.withColumn("prev_order_date", lag("order_date").over(windowSpec))
                                .withColumn("prev_tier_after_purchase", lag("tier_after_purchase").over(windowSpec)))



# expired_assets CTE
expired_assets = (previous_order_date
    .join(members_loyalty_expired_asset.alias("ea"), 
          (previous_order_date["acid"] == col("ea.acid")) & 
          (col("ea.expiry_date") > previous_order_date["prev_order_date"]) & 
          (col("ea.expiry_date") <= previous_order_date["order_date"]), "left")
    .select(previous_order_date["*"], col("ea.asset_type").alias("neg_tier_movement")))

# ranked_orders CTE
ranked_orders = (expired_assets.withColumn("rn", row_number().over(Window.partitionBy("acid").orderBy("order_date"))))

# Final DataFrame
final_df = (ranked_orders
    .select(
        "acid",
        "order_number",
        "tier_after_purchase",
        to_date("tier_date").alias("tier_date"),
        to_date("order_date").alias("order_date"),
        coalesce("tier_before_purchase_raw", lit(0)).alias("tier_before_purchase"),
        when(col("rn") == 1, "first_purchase")
        .when(coalesce("tier_before_purchase_raw", lit(0)) < coalesce("tier_after_purchase", lit(0)), "Upgrade")
        .when(coalesce("tier_before_purchase_raw", lit(0)) > coalesce("tier_after_purchase", lit(0)), "Downgrade")
        .when(coalesce("tier_before_purchase_raw", lit(0)) == coalesce("tier_after_purchase", lit(0)), "No Change")
        .otherwise("subsequent_purchase").alias("action_before_purchase"),
        max("neg_tier_movement").over(Window.partitionBy("acid", "order_number")).alias("neg_tier_movement")
    ))

# Now you can use final_df for further analysis or actions


In [0]:
final_df.createOrReplaceTempView("tier_at_purchase")

In [0]:
specific_user_df = spark.sql("SELECT * FROM tier_at_purchase WHERE acid = '004K2KV4OEU0OCOB'")
specific_user_df.show()

+----------------+--------------------+-------------------+----------+----------+--------------------+----------------------+-----------------+
|            acid|        order_number|tier_after_purchase| tier_date|order_date|tier_before_purchase|action_before_purchase|neg_tier_movement|
+----------------+--------------------+-------------------+----------+----------+--------------------+----------------------+-----------------+
|004K2KV4OEU0OCOB|44890000000101000...|                  2|2021-11-14|2022-04-13|                   2|             No Change|             NULL|
|004K2KV4OEU0OCOB|         AUK30094161|                  2|      NULL|2020-11-28|                   0|        first_purchase|             NULL|
|004K2KV4OEU0OCOB|         AUK31207140|                  2|      NULL|2020-12-20|                   0|               Upgrade|             NULL|
|004K2KV4OEU0OCOB|         AUK35386658|                  2|      NULL|2021-04-21|                   0|               Upgrade|           

In [0]:
user_df = specific_user_df.toPandas()

In [0]:
display(user_df)

acid order_number tier_after_purchase tier_date order_date tier_before_purchase action_before_purchase neg_tier_movement 004K2KV4OEU0OCOB 448900000001010000000000000004230513042022 2 2021-11-14 2022-04-13 2 No Change null 004K2KV4OEU0OCOB AUK30094161 2 null 2020-11-28 0 first_purchase null 004K2KV4OEU0OCOB AUK31207140 2 null 2020-12-20 0 Upgrade null 004K2KV4OEU0OCOB AUK35386658 2 null 2021-04-21 0 Upgrade null 004K2KV4OEU0OCOB AUK38693067 2 2021-04-23 2021-07-27 1 Upgrade null 004K2KV4OEU0OCOB AUK38711593 2 2021-04-23 2021-07-27 1 Upgrade null 004K2KV4OEU0OCOB AUK39164693 2 2021-04-23 2021-08-02 1 Upgrade null 004K2KV4OEU0OCOB AUK43530463 2 2021-04-23 2021-11-13 1 Upgrade null 004K2KV4OEU0OCOB AUK44125502 2 2021-11-14 2021-11-23 2 No Change null 004K2KV4OEU0OCOB AUK47305665 2 2021-11-14 2022-02-18 2 No Change null 004K2KV4OEU0OCOB AUK50279347 2 2021-11-14 2022-05-14 2 No Change null 004K2KV4OEU0OCOB AUK52476801 2 2021-11-14 2022-07-05 2 No Change null 004K2KV4OEU0OCOB AUK52705796 2 2021-11-14 2022-07-10 2 No Change null 004K2KV4OEU0OCOB AUK55440235 2 2021-11-14 2022-09-15 2 No Change null 004K2KV4OEU0OCOB AUK57214803 2 2021-11-14 2022-10-28 2 No Change null 004K2KV4OEU0OCOB AUK64058757 2 2022-12-01 2023-05-10 2 No Change TIER 004K2KV4OEU0OCOB AUK65941594 2 2022-12-01 2023-07-13 2 No Change null 004K2KV4OEU0OCOB AUK69125455 2 2022-12-01 2023-11-17 2 No Change null

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# Assuming members_loyalty_engagements, members_loyalty_tiers, and consumer_profile are already loaded as DataFrames

# Correcting ambiguous reference by specifying the table alias explicitly in the join conditions
# First, filter the consumer_profile DataFrame for non-null loyalty_memberid
consumer_profile_filtered = consumer_profile.filter(consumer_profile.loyalty_memberid.isNotNull())

# Join operations, ensuring we use aliases and specify columns unambiguously
tier_info = members_loyalty_engagements.alias('l') \
    .join(members_loyalty_tiers.alias('t'), 'acid', 'left_outer') \
    .join(consumer_profile_filtered.alias('cp'), 'acid', 'inner') \
    .filter((F.col('l.order_number').isNotNull()) & (F.col('l.engagement_date') > '2018-01-01')) \
    .groupBy('l.acid', 'l.order_number') \
    .agg(
        F.max('l.tier_details_id').alias('tier_after_purchase'),
        F.max(F.when(F.col('t.tier_achieved_date') <= F.col('l.engagement_date'), F.col('t.tier_details_id'))).alias('tier_before_purchase_raw'),
        F.max(F.when(F.col('t.tier_achieved_date') <= F.col('l.engagement_date'), F.col('t.tier_achieved_date'))).alias('tier_date'),
        F.max('l.engagement_date').alias('order_date')
    )

# Window specification for calculating previous order date and tier
windowSpec = Window.partitionBy('acid').orderBy('order_date')

# Calculating previous order date and tier
previous_order_date = tier_info.withColumn('prev_order_date', F.lag('order_date').over(windowSpec)) \
    .withColumn('prev_tier_after_purchase', F.lag('tier_after_purchase').over(windowSpec))

# Joining with members_loyalty_expired_asset for expired_assets
expired_assets = previous_order_date.alias('p') \
    .join(members_loyalty_expired_asset.alias('ea'), (F.col('p.acid') == F.col('ea.acid')) & (F.col('ea.expiry_date') > F.col('p.prev_order_date')) & (F.col('ea.expiry_date') <= F.col('p.order_date')), 'left_outer') \
    .select('p.acid', 'p.order_number', 'p.order_date', 'p.prev_order_date', 'p.tier_after_purchase', 'p.tier_before_purchase_raw', 'p.tier_date', 'p.prev_tier_after_purchase', F.col('ea.asset_type').alias('neg_tier_movement'))

# Assigning row numbers to orders
ranked_orders = expired_assets.withColumn('rn', F.row_number().over(windowSpec))

# Final selection and transformation
final_df = ranked_orders.select(
    'acid',
    'order_number',
    'tier_after_purchase',
    F.to_date('tier_date').alias('tier_date'),
    F.to_date('order_date').alias('order_date'),
    F.coalesce('tier_before_purchase_raw', F.lit(0)).alias('tier_before_purchase'),
    F.when(F.col('rn') == 1, 'first_purchase')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) < F.coalesce('tier_after_purchase', F.lit(0)), 'Upgrade')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) > F.coalesce('tier_after_purchase', F.lit(0)), 'Downgrade')
    .when(F.coalesce('tier_before_purchase_raw', F.lit(0)) == F.coalesce('tier_after_purchase', F.lit(0)), 'No Change')
    .otherwise('subsequent_purchase').alias('action_before_purchase'),
    F.max('neg_tier_movement').over(Window.partitionBy('acid', 'order_number')).alias('neg_tier_movement')
)

# Optional: Creating a temporary view for SQL-like querying
final_df.createOrReplaceTempView("loyalty_engage_tier_v15")





In [0]:
specific_user_df = spark.sql("SELECT * FROM loyalty_engage_tier_v15 WHERE acid = '004K2KV4OEU0OCOB'")
specific_user_df.show()

+----------------+--------------------+-------------------+----------+----------+--------------------+----------------------+-----------------+
|            acid|        order_number|tier_after_purchase| tier_date|order_date|tier_before_purchase|action_before_purchase|neg_tier_movement|
+----------------+--------------------+-------------------+----------+----------+--------------------+----------------------+-----------------+
|004K2KV4OEU0OCOB|44890000000101000...|                  2|2021-11-14|2022-04-13|                   2|             No Change|             NULL|
|004K2KV4OEU0OCOB|         AUK30094161|                  0|      NULL|2020-11-28|                   0|        first_purchase|             NULL|
|004K2KV4OEU0OCOB|         AUK31207140|                  0|      NULL|2020-12-20|                   0|             No Change|             NULL|
|004K2KV4OEU0OCOB|         AUK35386658|                  1|      NULL|2021-04-21|                   0|               Upgrade|           

In [0]:
display(specific_user_df)

acid order_number tier_after_purchase tier_date order_date tier_before_purchase action_before_purchase neg_tier_movement 004K2KV4OEU0OCOB 448900000001010000000000000004230513042022 2 2021-11-14 2022-04-13 2 No Change null 004K2KV4OEU0OCOB AUK30094161 0 null 2020-11-28 0 first_purchase null 004K2KV4OEU0OCOB AUK31207140 0 null 2020-12-20 0 No Change null 004K2KV4OEU0OCOB AUK35386658 1 null 2021-04-21 0 Upgrade null 004K2KV4OEU0OCOB AUK38693067 1 2021-04-23 2021-07-27 1 No Change null 004K2KV4OEU0OCOB AUK38711593 1 2021-04-23 2021-07-27 1 No Change null 004K2KV4OEU0OCOB AUK39164693 1 2021-04-23 2021-08-02 1 No Change null 004K2KV4OEU0OCOB AUK43530463 2 2021-04-23 2021-11-13 1 Upgrade null 004K2KV4OEU0OCOB AUK44125502 2 2021-11-14 2021-11-23 2 No Change null 004K2KV4OEU0OCOB AUK47305665 2 2021-11-14 2022-02-18 2 No Change null 004K2KV4OEU0OCOB AUK50279347 2 2021-11-14 2022-05-14 2 No Change null 004K2KV4OEU0OCOB AUK52476801 2 2021-11-14 2022-07-05 2 No Change null 004K2KV4OEU0OCOB AUK52705796 2 2021-11-14 2022-07-10 2 No Change null 004K2KV4OEU0OCOB AUK55440235 2 2021-11-14 2022-09-15 2 No Change null 004K2KV4OEU0OCOB AUK57214803 2 2021-11-14 2022-10-28 2 No Change null 004K2KV4OEU0OCOB AUK64058757 1 2022-12-01 2023-05-10 2 Downgrade TIER 004K2KV4OEU0OCOB AUK65941594 1 2022-12-01 2023-07-13 2 Downgrade null 004K2KV4OEU0OCOB AUK69125455 1 2022-12-01 2023-11-17 2 Downgrade null